In [1]:
import pandas as pd

from lets_plot import *
from lets_plot.geo_data import *

LetsPlot.setup_html()

The geodata is provided by © OpenStreetMap contributors and is made available here under the Open Database License (ODbL).


In [2]:
import lets_plot
lets_plot.__version__

'4.5.1'

In [3]:
income_dat = pd.read_csv('https://raw.githubusercontent.com/JetBrains/lets-plot-docs/master/data/US_household_income_2017.csv', encoding='latin-1')
income_dat.head(3)

id  State_Code State_Name State_ab          County        City  \
0  1011000           1    Alabama       AL   Mobile County   Chickasaw   
1  1011010           1    Alabama       AL  Barbour County  Louisville   
2  1011020           1    Alabama       AL   Shelby County  Columbiana   

             Place  Type Primary  Zip_Code Area_Code     ALand  AWater  \
0   Chickasaw city  City   place     36611       251  10894952  909156   
1        Clio city  City   place     36048       334  26070325   23254   
2  Columbiana city  City   place     35051       205  44835274  261034   

         Lat        Lon   Mean  Median  Stdev        sum_w  
0  30.771450 -88.079697  38773   30506  33101  1638.260513  
1  31.708516 -85.611039  37725   19528  43789   258.017685  
2  33.191452 -86.615618  54606   31930  57348   926.031000

In [4]:
income_dat = income_dat[~income_dat["State_Name"].isin(["Alaska", "Hawaii", "Puerto Rico"])]

In [5]:
income_dat = income_dat[income_dat["Mean"] > 0]
income_dat["Mean"].describe()

count     31606.000000
mean      67719.949883
std       29699.621113
min        5000.000000
25%       46827.000000
50%       61323.500000
75%       82669.750000
max      242857.000000
Name: Mean, dtype: float64

### Mean income by state

In [6]:
mean_income_state = income_dat.groupby("State_Name", as_index=False)["Mean"].mean()
mean_income_state.head(3)

State_Name          Mean
0    Alabama  54023.752874
1    Arizona  63400.114943
2   Arkansas  52213.932153

In [7]:
state_gcoder = geocode_states("US-48")
state_gcoder.get_geocodes().head(3)

id          state     found name                               centroid  \
0  60759        Vermont        Vermont   [-72.772353529363, 43.8718488067389]   
1  61315  Massachusetts  Massachusetts  [-72.0964509339039, 42.1913791447878]   
2  61320       New York       New York  [-76.0912327538441, 42.8993669897318]   

                                            position  \
0  [-73.4377402067184, 42.7269606292248, -71.4653...   
1  [-73.5082098841667, 41.4945808053017, -69.9292...   
2  [-79.7619438171387, 40.7823456823826, -73.2414...   

                                               limit  
0  [-73.4377402067184, 42.7269606292248, -71.4653...  
1  [-73.5082098841667, 41.2393619120121, -69.9292...  
2  [-79.7619438171387, 40.4960802197456, -71.8561...

In [8]:
ggplot() + geom_map(map=state_gcoder)

In [9]:
# Copy colors from Brewer's 'PiYG' palette: https://colorbrewer2.org/#type=diverging&scheme=PiYG&n=11
map_fill_colors = scale_fill_gradient2(low="#8e0152",mid="#f7f7f7",high="#276419", midpoint=67356)
map_settings = (theme(axis_line="blank", axis_text="blank", axis_title="blank", axis_ticks="blank") + 
                map_fill_colors + 
                coord_map() +
                ggsize(900, 400) )


In [10]:
(ggplot(mean_income_state) + 
 geom_polygon(aes(fill="Mean"), map=state_gcoder, map_join="State_Name", color="white") + 
 map_settings)

In [11]:
# inc_res
(ggplot(mean_income_state) + 
 geom_polygon(aes(fill="Mean"), map=state_gcoder.inc_res(2), map_join="State_Name", color="white") + 
 map_settings)

### Mean income by county


In [12]:
mean_income_county = income_dat.groupby(["State_Name","County"], as_index=False)["Mean"].mean()
mean_income_county.head(3)

State_Name          County          Mean
0    Alabama  Autauga County  54086.006522
1    Alabama  Barbour County  37725.000000
2    Alabama   Blount County  55127.000000

In [13]:
county_gcoder = (geocode_counties(mean_income_county["County"])
    .states(mean_income_county["State_Name"])
    .scope("us-48")
    .ignore_all_errors())
county_gcoder.get_geocodes().head(3)

id          county      found name    state  \
0  1848758  Autauga County  Autauga County  Alabama   
1  1850797  Barbour County  Barbour County  Alabama   
2  1848761   Blount County   Blount County  Alabama   

                                centroid  \
0  [-86.6511697368103, 32.5077094137669]   
1  [-85.3935062819253, 31.8834118545055]   
2  [-86.5330419226251, 34.0133339166641]   

                                            position  \
0  [-86.9211257994175, 32.3075589537621, -86.4111...   
1  [-85.7483513653278, 31.6182379424572, -85.0488...   
2  [-86.9634309411049, 33.7653543055058, -86.3030...   

                                               limit  
0  [-86.9211257994175, 32.3075589537621, -86.4111...  
1  [-85.7483513653278, 31.6182379424572, -85.0488...  
2  [-86.9634309411049, 33.7653543055058, -86.3030...

In [14]:
(ggplot(mean_income_county) + 
 geom_polygon(aes(fill="Mean"), map=county_gcoder, map_join=[["State_Name", "County"],['state', 'county']], color="white") + 
 map_settings)

### Bonus tracks

In [15]:
import numpy as np
from scipy.interpolate import griddata

def interpolate_us(lons, lats, values, step, method):
    # method : "linear", "cubic" or "nearest".
    
    # target grid to interpolate to
    grid_lons = np.arange(-125, -66, step)
    grid_lats = np.arange(25, 52, step)
    grid_lons, grid_lats = np.meshgrid(grid_lons, grid_lats)
    
    # interpolate
    grid_values = griddata((lons, lats), values, (grid_lons, grid_lats), method)

    return pd.DataFrame(dict(
            lon=grid_lons.flatten(), 
            lat=grid_lats.flatten(), 
            value=grid_values.flatten()))


#### Centroids to lon,lat

In [16]:
centroids_gdf = county_gcoder.get_centroids()
centroids_gdf.head(3)

county      found name    state                    geometry
0  Autauga County  Autauga County  Alabama  POINT (-86.65117 32.50771)
1  Barbour County  Barbour County  Alabama  POINT (-85.39351 31.88341)
2   Blount County   Blount County  Alabama  POINT (-86.53304 34.01333)

In [17]:
# merge with income
centroids_gdf = centroids_gdf.merge(mean_income_county, 
                                     left_on=["state", "county"], 
                                     right_on=["State_Name", "County"], how="left")
centroids_gdf.head(3)

county      found name    state                    geometry  \
0  Autauga County  Autauga County  Alabama  POINT (-86.65117 32.50771)   
1  Barbour County  Barbour County  Alabama  POINT (-85.39351 31.88341)   
2   Blount County   Blount County  Alabama  POINT (-86.53304 34.01333)   

  State_Name          County          Mean  
0    Alabama  Autauga County  54086.006522  
1    Alabama  Barbour County  37725.000000  
2    Alabama   Blount County  55127.000000

In [18]:
# Get lon, lat and income for interpolation
longitude = centroids_gdf.geometry.x
latitude = centroids_gdf.geometry.y
mean_income = centroids_gdf["Mean"]

In [19]:
mean_income_interpolated = interpolate_us(longitude, latitude, mean_income, .3, "linear")
mean_income_interpolated_nona = mean_income_interpolated.dropna(inplace=False)
mean_income_interpolated_nona.head(3)

lon   lat         value
538 -81.8  25.6  82562.373082
539 -81.5  25.6  83892.117004
540 -81.2  25.6  85221.860925

In [20]:
# US boundary
polygons_us = (geocode_countries("US")
             .get_boundaries(resolution="country")
             .explode())
polygons_us48 = polygons_us.cx[-125:-66, 25:52]

In [21]:
(ggplot(mean_income_interpolated_nona) + 
 geom_tile(aes("lon", "lat", fill="value"), height=1.4) + 
 geom_polygon(map=state_gcoder, color="black", size=0.3, alpha=0) + 
 geom_map(map=polygons_us48, size=2, color="#3E8DD2") +
 map_settings)

In [22]:
mean_income_interpolated["value"].describe()

count     11089.000000
mean      55489.544088
std       14233.968354
min       12656.312904
25%       45679.274798
50%       53356.945534
75%       62736.890134
max      147156.585935
Name: value, dtype: float64

In [23]:
mean_income_interpolated_fina = mean_income_interpolated.fillna(55538, inplace=False)

In [24]:
(ggplot(mean_income_interpolated_fina) + 
 geom_contour(aes("lon", "lat", z="value", color="..level.."), size=1, sampling="none") + 
 geom_polygon(map=state_gcoder, color="gray", alpha=0) + 
 geom_map(map=polygons_us48, size=2, color="#3E8DD2") +
 map_settings +
 scale_color_gradient2(low="#8e0152",mid="#f7f7f7",high="#276419", midpoint=67356))

In [25]:
(ggplot(mean_income_interpolated_fina) + 
 geom_contourf(aes("lon", "lat", z="value", fill="..level..")) + 
 geom_polygon(map=state_gcoder, color="black", size=0.3, alpha=0) + 
 geom_map(map=polygons_us48, size=2, color="#3E8DD2") +
 map_settings)

In [26]:
(ggplot(mean_income_interpolated_fina) + 
 geom_livemap() +
 geom_contourf(aes("lon", "lat", z="value", fill="..level..")) + 
 geom_polygon(map=state_gcoder, color="black", size=0.3, alpha=0) + 
 geom_map(map=polygons_us48, size=2, color="#3E8DD2") +
 map_settings)